In [106]:
from IPython import get_ipython
get_ipython().magic('reset -sf')


In [107]:
import numpy as np
import pandas as pd
from sklearn.preprocessing import StandardScaler
from sklearn.base import BaseEstimator, ClassifierMixin
from scipy.optimize import minimize, LinearConstraint, NonlinearConstraint
from scipy import stats
import pickle

In [108]:
## 划分测试集和训练集
train_ratio = 0.8 # 训练集比例

data = pd.read_csv('seeds_dataset.txt', header=None, delim_whitespace=True) # delim_whitespace=True表示分割符为空白字符
data.info

labels = data.iloc[:, -1]
classes = labels.unique()
trainData = pd.DataFrame(data=None, index=None)
testData = pd.DataFrame(data=None, index=None)

for i in classes:
    classData = data.loc[labels==i, :]
    numTrain = round(train_ratio*classData.shape[0]) # 训练集样本数
    indices = np.random.permutation(classData.shape[0])
    
    trainData = pd.concat([trainData, classData.iloc[indices[0:numTrain], :]])
    testData = pd.concat([testData, classData.iloc[indices[numTrain:], :]])

trainData.info
testData.info                                            
trainData.to_csv('trainData.csv', header=0, index=0, sep='\t')
testData.to_csv('testData.csv', header=0, index=0, sep='\t')


In [109]:
## 获取训练和训练数据及归一化
X_train = trainData.iloc[:, :-1]
Y_train = trainData.iloc[:, -1].values
X_test = testData.iloc[:, :-1]
Y_test = testData.iloc[:, -1].values

# 使用StandardScaler类归一化
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)


In [110]:
## 定义超圆盘分类器类
class NHCmodel(BaseEstimator, ClassifierMixin):
    def __init__(self, ) -> None:
        super().__init__()
        self.classes = 0
        self.s_r = {}
        self.classifiers = {}
        self.predictData = None
        self.accuracy = 0

    @staticmethod
    def gaussian_kernel(x, y, sigma=0.25):
        return np.exp(-np.linalg.norm(x-y, ord=2, axis=1)**2 / (2 * (sigma ** 2)))
    
    @staticmethod
    def Objective_Function1(beta, X):
        """返回超圆盘的对偶问题的目标函数，在某一拉格朗日系数下的值
        Args:
            beta (ndarray): 为该输入样本集合下的拉格朗日系数
            X (ndarray): X为输入样本矩阵, 行为样本个数, 列为样本特征
        """
        beta = beta.reshape(-1, 1)
        print(X)
        return np.sum(beta*np.sum(X*X, 1).reshape(-1, 1))-np.sum((beta*X)@((beta*X).T))
    
    @staticmethod
    def Objective_Function2(alpha, X_plus, X_minus):
        M_plus  = np.shape(X_plus)[0]
        alpha_plus = alpha[:M_plus]
        alpha_minus = alpha[M_plus:]
        M_minus = np.size(alpha_minus)
        result = 0
        for i in range(M_plus):
            result = result + np.sum(alpha_plus[i]*alpha_plus*NHCmodel.gaussian_kernel(X_plus[i, :], X_plus))
            - 2*np.sum(alpha_plus[i]*alpha_minus*NHCmodel.gaussian_kernel(X_plus[i, :], X_minus))
        for i in range(M_minus):
            result = result + np.sum(alpha_minus[i]*alpha_minus*NHCmodel.gaussian_kernel(X_minus[i, :], X_minus))
        return result
    
    @staticmethod
    def nonlcon(alpha, beta_plus, beta_minus, X_plus, X_minus, r_plus, r_minus):
        M_plus  = np.shape(X_plus)[0]
        alpha_plus = alpha[:M_plus]
        alpha_minus = alpha[M_plus:]
        M_minus = np.size(alpha_minus)
        
        c = np.zeros((2, 1))
        for i in range(M_plus):
            c[0] = c[0] + np.sum(alpha_plus[i]*alpha_plus*NHCmodel.gaussian_kernel(X_plus[i, :],X_plus))
            - np.sum(alpha_plus[i]*beta_plus*NHCmodel.gaussian_kernel(X_plus[i, :], X_plus))
            + np.sum(beta_plus[i]*beta_plus*NHCmodel.gaussian_kernel(X_plus[i, :], X_plus))
        c[0] -= r_plus**2
        for i in range(M_minus):
            c[0] = c[0] + np.sum(alpha_minus[i]*alpha_minus*NHCmodel.gaussian_kernel(X_minus[i, :],X_minus))
            - np.sum(alpha_minus[i]*beta_minus*NHCmodel.gaussian_kernel(X_minus[i, :], X_minus))
            + np.sum(beta_minus[i]*beta_minus*NHCmodel.gaussian_kernel(X_minus[i, :], X_minus))
        c[1] -= r_minus**2
        return c.flatten()

    def fit(self, X, y):
        # 拟合函数
        classes = np.unique(y)
        Num = np.size(classes)
        beta = np.zeros((Num, np.size(y)))
        s_and_r = np.ones((Num, np.shape(X)[1]+1))
        # 分类求解超圆盘对偶问题拉格朗日系数，以求解s和r
        for i in classes:
            Xx = X[y==i, :]
            M = np.shape(Xx)[0]
            # 设定拉格朗日系数beta初值,一个样本一个beta
            beta_init = np.ones((M, 1)) / M # 一维数组，但是在优化函数里面需要reshape乘二维数组才能运算
            # 设线性等式约束
            Aeq1 = np.ones((1, M))
            beq1 = np.array([1])
            linearConstraint1 = LinearConstraint(Aeq1, beq1, beq1)
            # 设定beta下界
            bounds = [(1e-6, None) for _ in range(M)] 
            # 求解beta
            result1 = minimize(NHCmodel.Objective_Function1, beta_init, 
                            args=(Xx,), method='SLSQP', bounds=bounds, constraints=linearConstraint1,
                            )
            beta[i-1, :M] = result1.x
            
            s = np.sum(result1.x.reshape(-1, 1)*Xx, 0)
            r = np.max(np.linalg.norm(Xx-s, ord=2,axis=1))
            s_and_r[i-1, :] = np.concatenate([s, [r]])
            
            self.s_r = {'s': s,
                        'r': r}
        # 求解多个分类器的参数，即分类超平面参数，OVO策略
        Num_classifier = int(Num*(Num-1)/2)
        b_classifier = np.zeros((Num_classifier, 1))
        iter = 0
        for i in range(Num-1):
            for j in range(i+1, Num):
                iter += 1
                # 获取基本信息
                X_plus = X[y==i+1, :]
                X_minus = X[y==j+1, :]
                M_plus = np.shape(X_plus)[0]
                M_minus = np.shape(X_minus)[0]
                # 设定超平面参数初值，都为列
                alpha_plus = np.ones((M_plus, 1)) / M_plus
                alpha_minus = np.ones((M_minus, 1)) / M_minus
                alpha_init = np.concatenate((alpha_plus, alpha_minus), axis=0)
                # 设定线性等式约束
                Aeq2 = np.zeros((2, M_plus+M_minus))
                Aeq2[0,:M_plus] = 1;
                Aeq2[1, M_plus:] = 1
                beq2 = np.array([1, 1])
                linearConstraint2 = LinearConstraint(Aeq2, beq2, beq2)
                # 设定不等式约束
                r_plus = s_and_r[i, -1]
                r_minus = s_and_r[j, -1]
                beta_plus = beta[i, :M_plus]
                beta_minus = beta[j, :M_minus]
                lb = -np.inf
                ub = np.array([0, 0])
                # NonlinearConstraint(lambda x: NHCmodel.nonlcon(x, beta_plus, beta_minus, X_plus, X_minus, r_plus_minus), lb, ub)
                # 这个和@(beta)Objective_Function1(beta, X),@(beta) 表示输入要优化的值为beta，X不动，异曲同工
                nonlinearConstraint =  NonlinearConstraint(lambda x: NHCmodel.nonlcon(x, beta_plus, beta_minus, X_plus, X_minus, r_plus, r_minus), lb, ub)
                constraints = [linearConstraint2, nonlinearConstraint]
                # 求解alpha
                result2 = minimize(NHCmodel.Objective_Function2, alpha_init, args=(X_plus, X_minus,),
                                   method='SLSQP', constraints=constraints)
                alpha = result2.x
                alpha_plus = alpha[:M_plus]
                alpha_minus = alpha[M_plus:]
                # 求解b
                for k in range(M_plus):
                    b_classifier[iter-1] += np.sum(alpha_plus[k]*alpha_plus*NHCmodel.gaussian_kernel(X_plus[k, :], X_plus))
                for k in range(M_minus):
                    b_classifier[iter-1] -= np.sum(alpha_minus[k]*alpha_minus*NHCmodel.gaussian_kernel(X_minus[k, :], X_minus))
                b_classifier[iter-1] = -1/2*b_classifier[iter-1]
                b = b_classifier[iter-1]
                self.classes = Num
                self.classifiers[(i+1, j+1)] = {'X+': X_plus,
                                                'X-': X_minus,
                                                'alpha+': alpha_plus,
                                                'alpha-': alpha_minus,
                                                'b': b}      
                # 保存分类器参数字典
                with open('classifiers.pkl', 'wb') as f:
                    pickle.dump(self.classifiers, f)
                                                        
                return 0

    def predict(self,X, y):
        fx = np.zeros((np.shape(X)[0], self.classes))
        indexclasses = 0
        fxij = np.zeros((np.shape(X)[0], self.classes))
        for (i, j), classifier in self.classifiers.items():
            indexclasses += 1
            X_pl = classifier['X+']
            X_mi = classifier['X-']
            alpha_pl = classifier['alpha+']
            alpha_mi = classifier['alpha-']
            bb = classifier['b']
            
            M_plus = np.shape(X_pl)[0]
            M_minus = np.shape(X_mi)[0]
            
            for g in range(M_plus):
                fx[:, indexclasses-1] = fx[:, indexclasses-1] + alpha_pl[g]*NHCmodel.gaussian_kernel(X_pl[g, :], X).reshape(-1)
            for g in range(M_minus):
                fx[:, indexclasses-1] = fx[:, indexclasses-1] - alpha_mi[g]*NHCmodel.gaussian_kernel(X_mi[g, :], X).reshape(-1)
            
            fx[:, indexclasses-1] = np.sign(fx[:, indexclasses-1] + bb)
            fx[:, indexclasses-1][fx[:, indexclasses-1]==1] = i
            fx[:, indexclasses-1][fx[:, indexclasses-1]==-1] = j
            fx[:, indexclasses-1][fx[:, indexclasses-1]==0] = 0
        

        y_pred = np.apply_along_axis(lambda x: np.argmax(np.bincount(x.astype(int))), axis=1, arr=fx) # axis表示假如你是n×m维度，axis=0，表示在n方向上，axis=1，表示在m方向上
        accuray = np.sum(y_pred==y) / np.size(y)
        y = y.reshape(-1, 1)
        y_pred = y_pred.reshape(-1, 1)
        self.predictData = np.concatenate((X, y, y_pred, fxij, fx), axis=1)
        self.accuracy = accuray
        print('accuray = ', accuray)
        return y_pred
              

In [111]:
## 训练
model = NHCmodel()
model.fit(X_train_scaled, Y_train)

C:\Users\lenovo\AppData\Local\Temp\ipykernel_9332\2215587945.py:79: DeprecationWarning: Use of `minimize` with `x0.ndim != 1` is deprecated. Currently, singleton dimensions will be removed from `x0`, but an error will be raised in SciPy 1.11.0.
  result1 = minimize(NHCmodel.Objective_Function1, beta_init,


[[-0.29681814 -0.54676507  2.02840217 -1.11260496  0.31049825  0.98725179
  -1.2367551 ]
 [-0.29012704 -0.2049595  -0.39106206 -0.0507084  -0.27725446 -1.02428732
  -0.55091987]
 [-0.93581851 -0.99259842 -0.22195972 -1.15594768 -0.85717046 -1.55900869
  -0.88504472]
 [-0.71835765 -0.60620952 -1.11516695 -0.47763416 -0.99823111 -0.14686423
  -0.67792639]
 [ 0.43920323  0.44149886  0.5801924   0.43473003  0.40976315 -1.90037694
  -0.20897923]
 [-0.1195039   0.02538773 -0.68590717  0.23535353 -0.394805   -1.51500419
   0.14273114]
 [-1.15662492 -1.26752899 -0.13957653 -1.35315704 -1.0818226  -0.70225438
  -1.57674179]
 [-0.19645159 -0.35357062  1.45171983 -0.7398576   0.19033547 -0.70292111
  -1.15078145]
 [ 0.12806692  0.20372107 -0.02250568  0.28303052  0.12502962 -1.02162038
  -0.37897258]
 [ 0.44254878  0.52323497  0.08155729  0.41956008  0.52208922 -0.62024599
   0.220889  ]
 [ 0.05781034  0.08483218  0.27667538  0.17250659  0.16682536 -1.08295999
  -0.10542007]
 [-0.70162989 -0.7399

d:\software\Anaconda3\lib\site-packages\scipy\optimize\_optimize.py:284: RuntimeWarning: Values in x were outside bounds during a minimize step, clipping to bounds
  warnings.warn("Values in x were outside bounds during a "
C:\Users\lenovo\AppData\Local\Temp\ipykernel_9332\2215587945.py:79: DeprecationWarning: Use of `minimize` with `x0.ndim != 1` is deprecated. Currently, singleton dimensions will be removed from `x0`, but an error will be raised in SciPy 1.11.0.
  result1 = minimize(NHCmodel.Objective_Function1, beta_init,


[[-0.29681814 -0.54676507  2.02840217 -1.11260496  0.31049825  0.98725179
  -1.2367551 ]
 [-0.29012704 -0.2049595  -0.39106206 -0.0507084  -0.27725446 -1.02428732
  -0.55091987]
 [-0.93581851 -0.99259842 -0.22195972 -1.15594768 -0.85717046 -1.55900869
  -0.88504472]
 [-0.71835765 -0.60620952 -1.11516695 -0.47763416 -0.99823111 -0.14686423
  -0.67792639]
 [ 0.43920323  0.44149886  0.5801924   0.43473003  0.40976315 -1.90037694
  -0.20897923]
 [-0.1195039   0.02538773 -0.68590717  0.23535353 -0.394805   -1.51500419
   0.14273114]
 [-1.15662492 -1.26752899 -0.13957653 -1.35315704 -1.0818226  -0.70225438
  -1.57674179]
 [-0.19645159 -0.35357062  1.45171983 -0.7398576   0.19033547 -0.70292111
  -1.15078145]
 [ 0.12806692  0.20372107 -0.02250568  0.28303052  0.12502962 -1.02162038
  -0.37897258]
 [ 0.44254878  0.52323497  0.08155729  0.41956008  0.52208922 -0.62024599
   0.220889  ]
 [ 0.05781034  0.08483218  0.27667538  0.17250659  0.16682536 -1.08295999
  -0.10542007]
 [-0.70162989 -0.7399

C:\Users\lenovo\AppData\Local\Temp\ipykernel_9332\2215587945.py:79: DeprecationWarning: Use of `minimize` with `x0.ndim != 1` is deprecated. Currently, singleton dimensions will be removed from `x0`, but an error will be raised in SciPy 1.11.0.
  result1 = minimize(NHCmodel.Objective_Function1, beta_init,


[[-1.07967723 -1.11148731 -0.60785993 -1.13644346 -1.0818226   0.97058341
  -0.54505803]
 [-1.23691816 -1.13377898 -1.94767077 -0.89372424 -1.49194338 -0.28087794
  -0.80688686]
 [-1.21015374 -1.15607065 -1.56177056 -0.96740686 -1.44753539  1.05459201
  -0.62907773]
 [-0.5209701  -0.46502895 -0.44309355 -0.19807364 -0.49929437  2.18804129
   0.05089565]
 [-0.56111672 -0.67308452  0.72761495 -0.85905007 -0.08394912  3.04146193
  -0.69941981]
 [-0.83545196 -0.83655675 -0.46043738 -0.89589138 -0.71872204  1.14593469
  -0.72091322]
 [-0.95923737 -0.7771123  -2.02138205 -0.49280411 -1.27512794  2.15937169
  -0.28127525]
 [-1.0261484  -0.82912619 -2.24251587 -0.47546703 -1.43186199  0.76322887
  -0.12105164]
 [-1.29044698 -1.1635012  -2.28153949 -0.66617498 -1.4710455   1.98802083
  -0.49034753]
 [-1.20680819 -1.26752899 -0.65989142 -1.17328477 -1.20198538  0.15449993
  -0.80688686]
 [-0.77857758 -0.73995952 -0.68157121 -0.64883789 -0.77357896  0.44386287
  -0.46494622]
 [-1.10978719 -0.9331

C:\Users\lenovo\AppData\Local\Temp\ipykernel_9332\2215587945.py:124: DeprecationWarning: Use of `minimize` with `x0.ndim != 1` is deprecated. Currently, singleton dimensions will be removed from `x0`, but an error will be raised in SciPy 1.11.0.
  result2 = minimize(NHCmodel.Objective_Function2, alpha_init, args=(X_plus, X_minus,),


0

In [112]:
# 测试
model.predict(X_test_scaled, Y_test)

accuray =  0.0


array([[0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [0],
       [0]], dtype=int64)